In [1]:
import anvil.server
import openai
import pathlib
import textwrap
import google.generativeai as genai #comment this for local deployment and uncomment dummy def below
import numpy as np

In [2]:
def compress_bool_list(bools):
    compressed_bits = np.packbits(bools,bitorder='big')
    return [compressed_bits,len(bools)]

def uncompress_bool_list(log):
    log[0]=np.array(log[0],dtype=np.uint8)
    return [bool(b) for b in np.unpackbits(log[0],bitorder='big')[:log[1]]]

In [14]:
def call_gemini(text,key):
    # response=f'calling gemini with key {key} and text {text}'
    # return response
    genai.configure(api_key=key)
    model = genai.GenerativeModel('gemini-1.5-flash')
    try:
        response = model.generate_content(text)
        retval=response.text
    except Exception as e:
        return -1,str(e)
    return 0,retval

In [4]:
def call_gpt(prompt,key,model):
    openai.api_key=key
    try:
        messages=[{"role": "system", "content": "You are a helpful assistant."}]
        messages+=[{"role": "user", "content": prompt}]
        completions=openai.chat.completions.create(  #for new version >.28 ) 
        # completions=openai.ChatCompletion.create(
        model=model,   
        messages=messages)
        # prediction=completions['choices'][0]['message']['content']
        prediction=completions.choices[0].message.content.strip() # for new version >.28
    except Exception as e:
        return -1,str(e)
    return 0,prediction